## 👉 START HERE: How to use this notebook

# Step 3: Build, evaluate, & deploy your Agent

Use this notebook to iterate on the code and configuration of your Agent.

By the end of this notebook, you will have 1+ registered versions of your Agent, each coupled with a detailed quality evaluation.

Optionally, you can deploy a version of your Agent that you can interact with in the [Mosiac AI Playground](https://docs.databricks.com/en/large-language-models/ai-playground.html) and let your business stakeholders who don't have Databricks accounts interact with it & provide feedback in the [Review App](https://docs.databricks.com/en/generative-ai/agent-evaluation/human-evaluation.html#review-app-ui).


For each version of your agent, you will have an MLflow run inside your MLflow experiment that contains:
- Your Agent's code & config
- Evaluation metrics for cost, quality, and latency


**Important note:** Throughout this notebook, we indicate which cell's code you:
- ✅✏️ should customize - these cells contain code & config with business logic that you should edit to meet your requirements & tune quality.
- 🚫✏️ should not customize - these cells contain boilerplate code required to load/save/execute your Agent

*Cells that don't require customization still need to be run!  You CAN change these cells, but if this is the first time using this notebook, we suggest not doing so.*

### 🚫✏️ Install Python libraries

You do not need to modify this cell unless you need additional Python packages in your Agent.

In [0]:
%pip install -qqqq -U -r requirements.txt
# # Restart to load the packages into the Python environment
dbutils.library.restartPython()

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
langchain 0.1.20 requires langchain-core<0.2.0,>=0.1.52, but you have langchain-core 0.3.26 which is incompatible.
langchain 0.1.20 requires langsmith<0.2.0,>=0.1.17, but you have langsmith 0.2.3 which is incompatible.
langchain-community 0.0.38 requires langchain-core<0.2.0,>=0.1.52, but you have langchain-core 0.3.26 which is incompatible.
langchain-community 0.0.38 requires langsmith<0.2.0,>=0.1.0, but you have langsmith 0.2.3 which is incompatible.
langchain-text-splitters 0.0.2 requires langchain-core<0.3,>=0.1.28, but you have langchain-core 0.3.26 which is incompatible.
ydata-profiling 4.5.1 requires pandas!=1.4.0,<2.1,>1.1, but you have pandas 2.2.3 which is incompatible.
ydata-profiling 4.5.1 requires pydantic<2,>=1.8.1, but you have pydantic 2.10.4 which is incompatible.
Note: you may need to restart the

### 🚫✏️ Connect to Databricks

If running locally in an IDE using Databricks Connect, connect the Spark client & configure MLflow to use Databricks Managed MLflow.  If this running in a Databricks Notebook, these values are already set.

In [0]:
from mlflow.utils import databricks_utils as du
import os

if not du.is_in_databricks_notebook():
    from databricks.connect import DatabricksSession

    spark = DatabricksSession.builder.getOrCreate()
    os.environ["MLFLOW_TRACKING_URI"] = "databricks"

### 🚫✏️ Load the Agent's UC storage locations; set up MLflow experiment

This notebook uses the UC model, MLflow Experiment, and Evaluation Set that you specified in the [Agent setup](02_agent_setup.ipynb) notebook.

In [0]:
from cookbook.config.shared.agent_storage_location import AgentStorageConfig
from cookbook.databricks_utils import get_mlflow_experiment_url
from cookbook.config import load_serializable_config_from_yaml_file
import mlflow 

# Load the Agent's storage locations
agent_storage_config: AgentStorageConfig= load_serializable_config_from_yaml_file("./configs/agent_storage_config.yaml")

# Show the Agent's storage locations
agent_storage_config.pretty_print()

# set the MLflow experiment
experiment_info = mlflow.set_experiment(agent_storage_config.mlflow_experiment_name)
# If running in a local IDE, set the MLflow experiment name as an environment variable
os.environ["MLFLOW_EXPERIMENT_NAME"] = agent_storage_config.mlflow_experiment_name

print(f"View the MLflow Experiment `{agent_storage_config.mlflow_experiment_name}` at {get_mlflow_experiment_url(experiment_info.experiment_id)}")

{
  "uc_model_name": "casaman_ssa.demos.my_agent_autogen",
  "evaluation_set_uc_table": "casaman_ssa.demos.my_agent_autogen_eval_set",
  "mlflow_experiment_name": "/Users/manffred.calvosanchez@databricks.com/my_agent_autogen_mlflow_experiment",
  "class_path": "cookbook.config.shared.agent_storage_location.AgentStorageConfig"
}
View the MLflow Experiment `/Users/manffred.calvosanchez@databricks.com/my_agent_autogen_mlflow_experiment` at https://adb-984752964297111.11.azuredatabricks.net/ml/experiments/2822477370659093


### 🚫✏️ Helper method to log the Agent's code & config to MLflow

Before we start, let's define a helper method to log the Agent's code & config to MLflow.  We will use this to log the agent's code & config to MLflow & the Unity Catalog.  It is used in evaluation & for deploying to Agent Evaluation's [Review App](https://docs.databricks.com/en/generative-ai/agent-evaluation/human-evaluation.html#review-app-ui) (a chat UI for your stakeholders to test this agent) and later, deplying the Agent to production.

In [0]:

import mlflow
from mlflow.types.llm import CHAT_MODEL_INPUT_SCHEMA
from mlflow.models.rag_signatures import StringResponse
from mlflow.models import ModelConfig
from cookbook.agents.utils.signatures import STRING_RESPONSE_WITH_MESSAGES
from mlflow.models.signature import ModelSignature
from cookbook.agents.function_calling_agent import FunctionCallingAgent
from cookbook.config.agents.function_calling_agent import FunctionCallingAgentConfig

# This helper will log the Agent's code & config to an MLflow run and return the logged model's URI
# If run from inside a mlfow.start_run() block, it will log to that run, otherwise it will log to a new run.
# This logged Agent is ready for deployment, so if you are happy with your evaluation, it is ready to deploy!
def log_function_calling_agent_to_mlflow(agent_config: FunctionCallingAgentConfig):
    # Get the agent's code path from the imported Agent class
    agent_code_path = f"{os.getcwd()}/{FunctionCallingAgent.__module__.replace('.', '/')}.py"

    # Get the pip requirements from the requirements.txt file
    with open("requirements.txt", "r") as file:
        pip_requirements = [line.strip() for line in file.readlines()] + ["pyspark"] # manually add pyspark

    logged_agent_info = mlflow.pyfunc.log_model(
            artifact_path="agent",
            python_model=agent_code_path,
            input_example=agent_config.input_example,
            model_config=agent_config.model_dump(),
            resources=agent_config.get_resource_dependencies(), # This allows the agents.deploy() command to securely provision credentials for the Agent's databricks resources e.g., vector index, model serving endpoints, etc
            signature=ModelSignature(
            inputs=CHAT_MODEL_INPUT_SCHEMA,
            # outputs=STRING_RESPONSE_WITH_MESSAGES #TODO: replace with MLflow signature
            outputs=StringResponse()
        ),
        code_paths=[os.path.join(os.getcwd(), "cookbook")],
        pip_requirements=pip_requirements,
    )

    return logged_agent_info

Exception ignored on calling ctypes callback function: <function _ThreadpoolInfo._find_modules_with_dl_iterate_phdr.<locals>.match_module_callback at 0x7fde57cdf6a0>
Traceback (most recent call last):
  File "/databricks/python/lib/python3.11/site-packages/threadpoolctl.py", line 400, in match_module_callback
    self._make_module_from_path(filepath)
  File "/databricks/python/lib/python3.11/site-packages/threadpoolctl.py", line 515, in _make_module_from_path
    module = module_class(filepath, prefix, user_api, internal_api)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/databricks/python/lib/python3.11/site-packages/threadpoolctl.py", line 606, in __init__
    self.version = self.get_version()
                   ^^^^^^^^^^^^^^^^^^
  File "/databricks/python/lib/python3.11/site-packages/threadpoolctl.py", line 646, in get_version
    config = get_config().split()
             ^^^^^^^^^^^^^^^^^^
AttributeError: 'NoneType' object has no attribute 'split'



## 1️⃣ Iterate on the Agent's code & config to improve quality

The below cells are used to execute your inner dev loop to improve the Agent's quality.

We suggest the following process:
1. Vibe check the Agent for 5 - 10 queries to verify it works
2. Make any necessary changes to the code/config
3. Use Agent Evaluation to evaluate the Agent using your evaluation set, which will provide a quality assessment & identify the root causes of any quality issues
4. Based on that evaluation, make & test changes to the code/config to improve quality
5. 🔁 Repeat steps 3 and 4 until you are satisified with the Agent's quality
6. Deploy the Agent to Agent Evaluation's [Review App](https://docs.databricks.com/en/generative-ai/agent-evaluation/human-evaluation.html#review-app-ui) for pre-production testing
7. Use the following notebooks to review that feedback (optionally adding new records to your evaluation set) & identify any further quality issues
8. 🔁 Repeat steps 3 and 4 to fix any issues identified in step 7
9. Deploy the Agent to a production-ready REST API endpoint (using the same cells in this notebook as step 6)


In [0]:
# Import Cookbook Agent configurations, which are Pydantic models
from cookbook.config import serializable_config_to_yaml_file
from cookbook.config.agents.function_calling_agent import (
    FunctionCallingAgentConfig,
)
from cookbook.config.data_pipeline import (
    DataPipelineConfig,
)
from cookbook.config.shared.llm import LLMConfig, LLMParametersConfig
from cookbook.config import load_serializable_config_from_yaml_file
from cookbook.tools.vector_search import (
    VectorSearchRetrieverTool,
    VectorSearchSchema,
)
from cookbook.tools.uc_tool import UCTool

import json
import mlflow
import yaml

########################
# #### 🚫✏️ Load the Vector Index Unity Cataloglocation from the data pipeline configuration
# Usage:
# - If you used `01_data_pipeline` to create your Vector Index, run this cell.
# - If your Vector Index was created elsewhere, comment out this logic and set the UC location in the Retriever config.
########################

#data_pipeline_config: DataPipelineConfig = #load_serializable_config_from_yaml_file(
#    "./configs/data_pipeline_config.yaml"
#)

########################
# #### ✅✏️ Retriever tool that connects to the Vector Search index
########################

retriever_tool = VectorSearchRetrieverTool(
    name="search_product_docs",
    description="Use this tool to search for product documentation.",
    vector_search_index="casaman_ssa.demos.test_product_docs_docs_chunked_index__v2",
    vector_search_schema=VectorSearchSchema(
        # These columns are the default values used in the `01_data_pipeline` notebook
        # If you used a different column names in that notebook OR you are using a pre-built vector index, update the column names here.
        chunk_text="content_chunked",  # Contains the text of each document chunk
        document_uri="doc_uri",  # The document URI of the chunk e.g., "/Volumes/catalog/schema/volume/file.pdf" - displayed as the document ID in the Review App
        # additional_metadata_columns=[],  # Additional columns to return from the vector database and present to the LLM
    ),
    # Optional parameters, see VectorSearchRetrieverTool.__doc__ for details.  The default values are shown below.
    # doc_similarity_threshold=0.0,
    # vector_search_parameters=VectorSearchParameters(
    #     num_results=5,
    #     query_type="ann"
    # ),
    # Adding columns here will allow the Agent's LLM to dynamically apply filters based on the user's query.
    # filterable_columns=[]
)

########################
# #### ✅✏️ Add Unity Catalog tools to the Agent
########################

translate_sku_tool = UCTool(uc_function_name="casaman_ssa.demos.sku_sample_translator")


########################
# #### ✅✏️ Add a local Python function as a tool in the Agent
########################

from cookbook.tools.local_function import LocalFunctionTool
from tools.sample_tool import sku_sample_translator

# translate_sku_tool = LocalFunctionTool(func=translate_sku, description="Translates a pre-2024 SKU formatted as 'OLD-XXX-YYYY' to the new SKU format 'NEW-YYYY-XXX'.")

tools = [retriever_tool, translate_sku_tool]

########################
#### ✅✏️ Agent's LLM configuration
########################

system_prompt = """
## Role
You are a helpful assistant that answers questions using a set of tools. If needed, you ask the user follow-up questions to clarify their request.

## Objective
Your goal is to provide accurate, relevant, and helpful response based solely on the outputs from these tools. You are concise and direct in your responses.

## Instructions
1. **Understand the Query**: Think step by step to analyze the user's question and determine the core need or problem. 

2. **Assess available tools**: Think step by step to consider each available tool and understand their capabilities in the context of the user's query.

3. **Select the appropriate tool(s) OR ask follow up questions**: Based on your understanding of the query and the tool descriptions, decide which tool(s) should be used to generate a response. If you do not have enough information to use the available tools to answer the question, ask the user follow up questions to refine their request.  If you do not have a relevant tool for a question or the outputs of the tools are not helpful, respond with: "I'm sorry, I can't help you with that."
""".strip()

fc_agent_config = FunctionCallingAgentConfig(
    llm_config=LLMConfig(
        llm_endpoint_name="databricks-meta-llama-3-3-70b-instruct",  # Model serving endpoint w/ a Chat Completions API
        llm_system_prompt_template=system_prompt,  # System prompt template
        llm_parameters=LLMParametersConfig(
            temperature=0.01, max_tokens=1500
        ),  # LLM parameters
    ),
    # Add one or more tools that comply with the CookbookTool interface
    tools=tools,
)

# Print the configuration as a JSON string to see it all together
# print(json.dumps(fc_agent_config.model_dump(), indent=4))

########################
##### Dump the configuration to a YAML
# Optional step, this allows the Agent's code file to be run by itself (e.g., outside of this notebook) using the above configuration.
########################
# Import the default YAML config file name from the Agent's code file
from cookbook.agents.function_calling_agent import FC_AGENT_DEFAULT_YAML_CONFIG_FILE_NAME

# Dump the configuration to a YAML file
serializable_config_to_yaml_file(fc_agent_config, "./configs/"+FC_AGENT_DEFAULT_YAML_CONFIG_FILE_NAME)

#### ✅✏️ Optionally, adjust the Agent's code

Here, we import the Agent's code so we can run the Agent locally within the notebook.  To modify the code, open the Agent's code file in a separate window, enable reload, make your changes, and re-run this cell.

**Typically, when building the first version of your agent, we suggest first trying to tune the configuration (prompts, etc) to improve quality.  If you need more control to fix quality issues, you can then modify the Agent's code.**

In [0]:
from cookbook.agents.function_calling_agent import FunctionCallingAgent
import inspect

# Print the Agent code for inspection
print(inspect.getsource(FunctionCallingAgent))

class FunctionCallingAgent(mlflow.pyfunc.PythonModel):
    """
    Class representing an Agent that does function-calling with tools using Autogen
    """

    def __init__(
        self,
        agent_config: Optional[Union[FunctionCallingAgentConfig, str]] = None
    ):
        super().__init__()
        # Empty variables that will be initialized after loading the agent config.
        self.agent_config = None
        self.tools = None

        # load the Agent's configuration. See load_config() for details.
        self.agent_config = load_config(
            passed_agent_config=agent_config,
            default_config_file_name=FC_AGENT_DEFAULT_YAML_CONFIG_FILE_NAME,
        )
        if not self.agent_config:
            logging.error(
                f"No agent config found.  If you are in your local development environment, make sure you either [1] are calling init(agent_config=...) with either an instance of FunctionCallingAgentConfig or the full path to a YAML config file or [

In [0]:
%load_ext autoreload
%autoreload 3

#### ✅✏️ 🅰 Vibe check the Agent for a single query

Running this cell will produce an MLflow Trace that you can use to see the Agent's outputs and understand the steps it took to produce that output.

If you are running in a local IDE, browse to the MLflow Experiment page to view the Trace (link to the Experiment UI is at the top of this notebook).  If running in a Databricks Notebook, your trace will appear inline below.

In [0]:
from cookbook.databricks_utils import get_mlflow_experiment_traces_url
from cookbook.agents.function_calling_agent import FunctionCallingAgent

# Load the Agent's code with the above configuration
agent = FunctionCallingAgent(agent_config=fc_agent_config)

# Vibe check the Agent for a single query
output = agent.predict(model_input={"messages": [{"role": "user", "content": "What is mlflow in databricks?"}]})
# output = agent.predict(model_input={"messages": [{"role": "user", "content": "Translate the sku `OLD-abs-1234` to the new format"}]})

print(f"View the MLflow Traces at {get_mlflow_experiment_traces_url(experiment_info.experiment_id)}")
print(f"Agent's final response:\n----\n{output['content']}\n----")
print()
# print(f"Agent's full message history (useful for debugging):\n----\n{json.dumps(output['messages'], indent=2)}\n----")


[autogen.oai.client: 12-18 17:42:54] {509} INFO - Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


INFO:autogen.oai.client:Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


[autogen.oai.client: 12-18 17:42:54] {509} INFO - Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


INFO:autogen.oai.client:Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


[autogen.oai.client: 12-18 17:42:54] {509} INFO - Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


INFO:autogen.oai.client:Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


User (to Assistant):

What is mlflow in databricks?

--------------------------------------------------------------------------------

>>>>>>>> USING AUTO REPLY...
Assistant (to User):

***** Suggested tool call (call_9a1e76b7-0b7f-4598-92f4-c5784c31e556): search_product_docs *****
Arguments: 
{ "query": "mlflow in databricks", "filters": [] }
************************************************************************************************

--------------------------------------------------------------------------------

>>>>>>>> EXECUTING FUNCTION search_product_docs...
User (to Assistant):

User (to Assistant):

***** Response from calling tool (call_9a1e76b7-0b7f-4598-92f4-c5784c31e556) *****
[{"page_content": "build models iteratively and deploy across\n\nmultiple platforms\n\n\n-----\n\n**M A C H I N E L E A R N I N G L I F E C Y C L E**\n\n###### Providing managed MLflow on Databricks\n\nMLflow is natively integrated with the Databricks Unified Data Analytics Platform so that ML p

Trace(request_id=tr-32320289e5be4eea8fd73d53e02c7e87)

Now, let's test a multi-turn conversation with the Agent.

In [0]:
output['content']

'MLflow is a platform that helps manage the machine learning lifecycle, and it is natively integrated with the Databricks Unified Data Analytics Platform. It provides features such as experiment tracking, reproducible projects, and model packaging, and is designed to be open and extensible. MLflow on Databricks offers an integrated experience for tracking and securing machine learning model training runs and running machine learning projects. It also provides a fully managed and hosted version of MLflow with enterprise security features, high availability, and other Databricks workspace features. Additionally, MLflow has built-in integrations with popular machine learning libraries and frameworks, and supports multiple programming languages.'

In [0]:
second_turn = {'messages': output['messages'] + [{"role": "user", "content": "How can I use it for versioning my model?"}]}

# Run the Agent again with the same input to continue the conversation
second_turn_output = agent.predict(model_input=second_turn)

print(f"View the MLflow Traces at {get_mlflow_experiment_traces_url(experiment_info.experiment_id)}")
print(f"Agent's final response:\n----\n{second_turn_output['content']}\n----")
print()
print(f"Agent's full message history (useful for debugging):\n----\n{json.dumps(second_turn_output['messages'], indent=2)}\n----")

[autogen.oai.client: 12-18 17:43:10] {509} INFO - Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


INFO:autogen.oai.client:Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


[autogen.oai.client: 12-18 17:43:10] {509} INFO - Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


INFO:autogen.oai.client:Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


[autogen.oai.client: 12-18 17:43:10] {509} INFO - Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


INFO:autogen.oai.client:Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


User (to Assistant):

How can I use it for versioning my model?

--------------------------------------------------------------------------------

>>>>>>>> USING AUTO REPLY...
Assistant (to User):

***** Suggested tool call (call_a6a5d604-8249-4f2f-a38a-340d5e923d42): search_product_docs *****
Arguments: 
{ "query": "MLflow versioning model", "filters": [] }
************************************************************************************************

--------------------------------------------------------------------------------

>>>>>>>> EXECUTING FUNCTION search_product_docs...
User (to Assistant):

User (to Assistant):

***** Response from calling tool (call_a6a5d604-8249-4f2f-a38a-340d5e923d42) *****
[{"page_content": "**Parameters**\n\n\n**Metrics** **Artifacts**\n\n\nThe Model Registry gives MLflow users new\n\n\ntools for sharing, reviewing and managing\n\nML models throughout their lifecycle\n\n\n**Metadata** **Models**\n\n**R E S T S E R V I N G**\n\n**R E V I E W E R S +

Trace(request_id=tr-df75a507fff24a89a1e45772ab840e22)

#### ✅✏️ 🅱 Evaluate the Agent using your evaluation set

Note: If you do not have an evaluation set, you can create a synthetic evaluation set by using the 03_synthetic_evaluation notebook.

In [0]:
evaluation_set = spark.table(agent_storage_config.evaluation_set_uc_table)

mlflow.langchain.autolog(disable=True, log_traces=False)
mlflow.autogen.autolog(log_traces=False)

with mlflow.start_run():
    logged_agent_info = log_function_calling_agent_to_mlflow(fc_agent_config)

    # Run the agent for these queries, using Agent evaluation to parallelize the calls
    eval_results = mlflow.evaluate(
        model=logged_agent_info.model_uri,  # use the MLflow logged Agent
        data=evaluation_set,  # Evaluate the Agent for every row of the evaluation set
        model_type="databricks-agent",  # use Agent Evaluation
    )

    # Show all outputs.  Click on a row in this table to display the MLflow Trace.
    display(eval_results.tables["eval_results"])

    # Click 'View Evaluation Results' to see the Agent's inputs/outputs + quality evaluation displayed in a UI

2024/12/18 17:43:29 WARNING mlflow.utils.autologging_utils: MLflow autogen autologging is known to be compatible with 0.2.36 <= autogen-agentchat <= 0.2.39, but the installed version is 0.2.40. If you encounter errors during autologging, try upgrading / downgrading autogen-agentchat to a compatible version, or try upgrading MLflow.
/root/.ipykernel/10605/command-2822477370486938-337563765:30: FutureWarning: ``mlflow.models.rag_signatures.StringResponse`` is deprecated. This method will be removed in a future release. Use ``mlflow.types.llm.ChatCompletionResponse`` instead.
  outputs=StringResponse()


[autogen.oai.client: 12-18 17:43:36] {509} INFO - Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


INFO:autogen.oai.client:Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


[autogen.oai.client: 12-18 17:43:36] {509} INFO - Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


INFO:autogen.oai.client:Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


...

User (to Assistant):

What are the main advantages of the lakehouse architecture over traditional on-premises data warehouses and cloud data warehouses?

--------------------------------------------------------------------------------

>>>>>>>> USING AUTO REPLY...
Assistant (to User):

According to the search results, the implementation of digital-twin technology in automobile manufacturing has led to reported increases in profit margins of 41% to 54% per model, and a reduction in manufacturing time of approximately 10 hours.

--------------------------------------------------------------------------------
Assistant (to User):

***** Suggested tool call (call_5daaee03-ba46-4038-bb14-1189c8d60f61): search_product_docs *****
Arguments: 
{ "query": "critical needs for IT and business when implementing a customer data platform", "filters": [] }
************************************************************************************************

-------------------------------------------------

<!DOCTYPE html>
 
 
 Evaluation output 
 
 
 
 
 
 
 
 <!-- AI icon -->
 
 
 <path fill="currentColor" fill-rule="evenodd"
 d="M4 9a.75.75 0 0 1 .739.621l.152.877a.75.75 0 0 0 .61.61l.878.153a.75.75 0 0 1 0 1.478l-.877.152a.75.75 0 0 0-.61.61l-.153.878a.75.75 0 0 1-1.478 0l-.152-.877a.75.75 0 0 0-.61-.61l-.878-.153a.75.75 0 0 1 0-1.478l.877-.152a.75.75 0 0 0 .61-.61l.153-.878A.75.75 0 0 1 4 9Zm0 2.92a2.289 2.289 0 0 1-.08.08c.028.026.054.052.08.08.026-.028.052-.054.08-.08a2.289 2.289 0 0 1-.08-.08ZM10 0c.36 0 .67.257.737.611l.264 1.398A3.75 3.75 0 0 0 13.99 5l1.398.264a.75.75 0 0 1 0 1.474l-1.398.264A3.75 3.75 0 0 0 11 9.99l-.264 1.398a.75.75 0 0 1-1.474 0l-.264-1.398A3.75 3.75 0 0 0 6.01 7l-1.398-.264a.75.75 0 0 1 0-1.474l1.398-.264A3.75 3.75 0 0 0 9 2.01L9.263.611A.75.75 0 0 1 10 0Zm0 3.682A5.256 5.256 0 0 1 7.682 6 5.256 5.256 0 0 1 10 8.318 5.256 5.256 0 0 1 12.318 6 5.256 5.256 0 0 1 10 3.682Z"
 clip-rule="evenodd"> 
 
 Evaluation completed: 5/19 pass all assessments 
 
 
 
 
 ℹ️ 8/19 could not run model 
 
 ℹ️ 1/19 could not run all selected judges 
 
 
 
 
 
 
 <!-- "Open in a new tab" icon -->
 
 
 
 
 View evaluation results
 
 
 
 <!-- "Open in a new tab" icon -->
 
 
 
 
 Compare evaluations across runs
 
 
 
 
 Python APIs: 
 
 mlflow.evaluate() returns a result object that is an instance of EvaluationResult . 
 
 
 result.metrics : A dictionary of aggregated evaluation results.
 
 
 result.tables['eval_results'] : A DataFrame of per-request evaluation results.
 
 

 
 For more details, see the mlflow.evaluate 
 API reference or the MLflow
 LLM Evaluate Quickstart .

2024/12/18 17:44:45 WARNING mlflow.utils.autologging_utils: MLflow autogen autologging is known to be compatible with 0.2.36 <= autogen-agentchat <= 0.2.39, but the installed version is 0.2.40. If you encounter errors during autologging, try upgrading / downgrading autogen-agentchat to a compatible version, or try upgrading MLflow.


request_id request expected_retrieved_context expected_facts trace model_error_message source_id response response/overall_assessment/rating response/overall_assessment/rationale response/llm_judged/safety/rating response/llm_judged/safety/rationale response/llm_judged/correctness/rating response/llm_judged/correctness/rationale agent/latency_seconds agent/total_token_count agent/total_input_token_count agent/total_output_token_count retrieval/llm_judged/context_sufficiency/error_message response/llm_judged/groundedness/error_message retrieved_context response/llm_judged/groundedness/rating response/llm_judged/groundedness/rationale retrieval/llm_judged/context_sufficiency/rating retrieval/llm_judged/context_sufficiency/rationale retrieval/ground_truth/document_ratings retrieval/ground_truth/document_recall 21866cbed9a5ba0daafc9367a06f6679f7e6290dd05b59cfd45d36fdbc8fbe73 List(List(List(Why is it recommended to use larger clusters for workloads in Databricks, and how does this affect cost efficiency?, user))) List(List(**EBOOK**

## The Big Book of Data Engineering 2nd Edition

A collection of technical
blogs, including code
samples and notebooks

##### With all-new content


-----

#### Contents

**S E CTI ON 1** **Introduction to Data Engineering on Databricks** ............................................................................................................. **03**

**S E CTI ON 2** **Guidance and Best Practices** ........................................................................................................................................................................... **10**

**2 .1** Top 5 Databricks Performance Tips ................................................................................................................................................. 11

**2 . 2** How to Profile PySpark ........................................................................................................................................................................ 16

**2 . 3** Low-Latency Streaming Data Pipelines With Delta Live Tables and Apache Kafka .......................................................... 20

**2 . 4** Streaming in Production: Collected Best Practices ................................................................................................................... 25

**2 . 5** Streaming in Production: Collected Best Practices, Part 2 ...................................................................................................... 32

**2 .6** Building Geospatial Data Products ................................................................................................................................................. 37

**2 .7** Data Lineage With Unity Catalog .................................................................................................................................................... 47

**2 . 8** Easy Ingestion to Lakehouse With COPY INTO ............................................................................................................................ 50

**2 .9** Simplifying Change Data Capture With Databricks Delta Live Tables .................................................................................. 57

**2 .1 0** Best Practices for Cross-Government Data Sharing ................................................................................................................. 65

**S E CTI ON 3** **Ready-to-Use Notebooks and Data Sets** ...................................................................................................................................... **74**

**S E CTI ON 4** **Case Studies** ................................................................................................................................................................................................................................. **76**

**4 . 1** Akamai ......................................................................

🏃 View run amusing-robin-418 at: https://adb-984752964297111.11.azuredatabricks.net/ml/experiments/2822477370659093/runs/daf417a2ec4a4ebaa7ba9622535a6263
🧪 View experiment at: https://adb-984752964297111.11.azuredatabricks.net/ml/experiments/2822477370659093


## 2️⃣ Deploy a version of your Agent - either to the Review App or Production

Once you have a version of your Agent that has sufficient quality, you will register the Agent's model from the MLflow Experiment into the Unity Catalog & use Agent Framework's `agents.deploy(...)` command to deploy it.  Note these steps are the same for deploying to pre-production (e.g., the [Review App](https://docs.databricks.com/en/generative-ai/agent-evaluation/human-evaluation.html#review-app-ui) or production.

By the end of this step, you will have deployed a version of your Agent that you can interact with and share with your business stakeholders for feedback, even if they don't have access to your Databricks workspace:

1. A production-ready scalable REST API deployed as a Model Serving endpoint that logged every request/request/MLflow Trace to a Delta Table.
    - REST API for querying the Agent
    - REST API for sending user feedback from your UI to the Agent
2. Agent Evaluation's [Review App](https://docs.databricks.com/en/generative-ai/agent-evaluation/human-evaluation.html#review-app-ui) connected to these endpoints.
3. [Mosiac AI Playground](https://docs.databricks.com/en/large-language-models/ai-playground.html) connected to these endpoints.

Option 1: Deploy the last agent you logged above

In [0]:
from databricks import agents

# Use Unity Catalog as the model registry
mlflow.set_registry_uri("databricks-uc")

# Register the Agent's model to the Unity Catalog
uc_registered_model_info = mlflow.register_model(
    model_uri=logged_agent_info.model_uri, name=agent_storage_config.uc_model_name
)

# Deploy the model to the review app and a model serving endpoint
agents.deploy(agent_storage_config.uc_model_name, uc_registered_model_info.version)

Registered model 'casaman_ssa.demos.my_agent_autogen' already exists. Creating a new version of this model...
Created version '15' of model 'casaman_ssa.demos.my_agent_autogen'.
/local_disk0/.ephemeral_nfs/envs/pythonEnv-d1adea7d-6539-428e-9e3a-1dc2ec857a07/lib/python3.11/site-packages/databricks/agents/utils/mlflow_utils.py:130: FutureWarning: ``mlflow.models.rag_signatures.ChatCompletionRequest`` is deprecated. This method will be removed in a future release. Use ``mlflow.types.llm.ChatCompletionRequest`` instead.
  ChatCompletionRequest()
/local_disk0/.ephemeral_nfs/envs/pythonEnv-d1adea7d-6539-428e-9e3a-1dc2ec857a07/lib/python3.11/site-packages/mlflow/models/rag_signatures.py:26: FutureWarning: ``mlflow.models.rag_signatures.Message`` is deprecated. This method will be removed in a future release. Use ``mlflow.types.llm.ChatMessage`` instead.
  messages: list[Message] = field(default_factory=lambda: [Message()])
/local_disk0/.ephemeral_nfs/envs/pythonEnv-d1adea7d-6539-428e-9e3a-1dc


    Deployment of casaman_ssa.demos.my_agent_autogen version 15 initiated.  This can take up to 15 minutes and the Review App & Query Endpoint will not work until this deployment finishes.

    View status: https://adb-984752964297111.11.azuredatabricks.net/ml/endpoints/agents_casaman_ssa-demos-my_agent_autogen
    Review App: https://adb-984752964297111.11.azuredatabricks.net/ml/review/casaman_ssa.demos.my_agent_autogen/15?o=984752964297111
    


Deployment(model_name='casaman_ssa.demos.my_agent_autogen', model_version='15', endpoint_name='agents_casaman_ssa-demos-my_agent_autogen', served_entity_name='casaman_ssa-demos-my_agent_autogen_15', query_endpoint='https://adb-984752964297111.11.azuredatabricks.net/serving-endpoints/agents_casaman_ssa-demos-my_agent_autogen/served-models/casaman_ssa-demos-my_agent_autogen_15/invocations', endpoint_url='https://adb-984752964297111.11.azuredatabricks.net/ml/endpoints/agents_casaman_ssa-demos-my_agent_autogen', review_app_url='https://adb-984752964297111.11.azuredatabricks.net/ml/review/casaman_ssa.demos.my_agent_autogen/15?o=984752964297111')

Option 2: Log the latest copy of the Agent's code/config and deploy it

In [0]:
from databricks import agents

# Use Unity Catalog as the model registry
mlflow.set_registry_uri("databricks-uc")

with mlflow.start_run():
    logged_agent_info = log_function_calling_agent_to_mlflow(fc_agent_config)

    # Register the Agent's model to the Unity Catalog
    uc_registered_model_info = mlflow.register_model(
        model_uri=logged_agent_info.model_uri, name=agent_storage_config.uc_model_name
    )

# Deploy the model to the review app and a model serving endpoint
# agents.deploy(agent_storage_config.uc_model_name, uc_registered_model_info.version)

com.databricks.backend.common.rpc.CommandCancelledException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$5(SequenceExecutionState.scala:136)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:136)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:728)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:446)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:446)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.can

Load the logged model to test it locally

In [0]:
mlflow.autogen.autolog(log_traces=False)

2024/12/18 17:45:54 WARNING mlflow.utils.autologging_utils: MLflow autogen autologging is known to be compatible with 0.2.36 <= autogen-agentchat <= 0.2.39, but the installed version is 0.2.40. If you encounter errors during autologging, try upgrading / downgrading autogen-agentchat to a compatible version, or try upgrading MLflow.


In [0]:
import mlflow

loaded_model = mlflow.pyfunc.load_model(logged_agent_info.model_uri)

loaded_model.predict({"messages": [{"role": "user", "content": "A test question?"}]})

[autogen.oai.client: 12-18 17:46:07] {509} INFO - Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


INFO:autogen.oai.client:Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


[autogen.oai.client: 12-18 17:46:07] {509} INFO - Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


INFO:autogen.oai.client:Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


[autogen.oai.client: 12-18 17:46:07] {509} INFO - Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


INFO:autogen.oai.client:Detected custom model client in config: DatabricksModelServingClient, model client can not be used until register_model_client is called.


User (to Assistant):

A test question?

--------------------------------------------------------------------------------

>>>>>>>> USING AUTO REPLY...
Assistant (to User):

I'm sorry, I can't help you with that.

--------------------------------------------------------------------------------


{'content': "I'm sorry, I can't help you with that.",
 'messages': [{'content': 'A test question?', 'role': 'user'},
  {'content': "I'm sorry, I can't help you with that.",
   'role': 'assistant',
   'name': 'Assistant'}]}

Trace(request_id=tr-c1ef3a3fa91341f683b3746e4c6fe29e)